## Dependencies

In [2]:
import torch
import subprocess
import time

In [ ]:
WORLD_SIZE = 2

In [ ]:

# configs
torch.cuda.empty_cache()
torch.cuda.synchronize()
NUM_CONTAINERS = WORLD_SIZE
IMAGE_NAME = "moe_expert"
BASE_PORT = 5000
layer = 1
experts_count_per_container = 8//NUM_CONTAINERS

docker_start_time = time.time() 

for i in range(NUM_CONTAINERS):
    cmd = [
    "docker", "run", "-d",
    "--name", f"layer{layer}_exp_{i*experts_count_per_container}_{(i+1)*experts_count_per_container-1}",
    "--gpus", "all",
    "--rm",
    "-p", f"{BASE_PORT+i}:5000",
    
    "-v", "/root/MG_test/mixtral/mixtral-mcore-TP1PP1EP2Layer1:/app/weights",
    "-v", "/root/MG_test/mixtral/REPLICATE/saved_objects:/app/saved_objects",
    "-e", f"RANK={i}",
    "-e", f"NUM_LOCAL_EXPERTS={experts_count_per_container}",
    "-e", f"GPU_IDX={0}",
    "-e", f"WEIGHT_PATH=/app/weights",
    "-e", f"PATH_SAVEDOBJ=/app/saved_objects",
    "-e", f"LAYER={layer}",
    "-e", f"WARMUP={True}",
    
    
    IMAGE_NAME
    ]
    try:
        subprocess.run(cmd, check=True)
        print(f"fused_moe_layer_{layer}_exp_{i*experts_count_per_container}_{(i+1)*experts_count_per_container-1}\n容器启动成功！")
    except subprocess.CalledProcessError as e:
        print(f"启动失败: {e}")
        
    # duplicated container    
    cmd = [
    "docker", "run", "-d",
    "--name", f"layer{layer}_exp_{(i+NUM_CONTAINERS)*experts_count_per_container}_{(i+NUM_CONTAINERS+1)*experts_count_per_container-1}",
    "--gpus", "all",
    "--rm",
    "-p", f"{BASE_PORT+i+NUM_CONTAINERS}:5000",
    
    "-v", "/root/MG_test/mixtral/mixtral-mcore-TP1PP1EP2Layer1:/app/weights",
    "-v", "/root/MG_test/mixtral/REPLICATE/saved_objects:/app/saved_objects",
    "-e", f"RANK={i}",
    "-e", f"NUM_LOCAL_EXPERTS={experts_count_per_container}",
    "-e", f"GPU_IDX={0}",
    "-e", f"WEIGHT_PATH=/app/weights",
    "-e", f"PATH_SAVEDOBJ=/app/saved_objects",
    "-e", f"LAYER={layer}",
    "-e", f"WARMUP={True}",
    # "-e", f"LOADED_EXPERTS={list(range(i*experts_count_per_container,(i+1)*experts_count_per_container))}",

    
    
    IMAGE_NAME
    ]
    try:
        subprocess.run(cmd, check=True)
        print(f"fused_moe_layer_{layer}_exp_{(i+NUM_CONTAINERS)*experts_count_per_container}_{(i+NUM_CONTAINERS+1)*experts_count_per_container-1}\n容器启动成功！")
    except subprocess.CalledProcessError as e:
        print(f"启动失败: {e}")
        

end_time = time.time()  # 记录结束时间
elapsed_time = end_time - docker_start_time  # 计算用时
print(f"Containers launched in: {elapsed_time*1000:.2f} ms")
print(f"Average containers launching time : {elapsed_time*1000/WORLD_SIZE:.2f} ms")

In [ ]:
import pickle
RANK=0
with open(f"/root/MG_test/mixtral/REPLICATE/saved_objects/rank_{RANK}/args.pickle", 'rb') as f:
    args = pickle.load(f)



Namespace(num_layers=1, encoder_num_layers=1, decoder_num_layers=None, hidden_size=4096, ffn_hidden_size=14336, num_attention_heads=32, attention_backend=<AttnBackend.auto: 5>, kv_channels=128, group_query_attention=True, num_query_groups=8, max_position_embeddings=32768, position_embedding_type='rope', relative_attention_num_buckets=32, relative_attention_max_distance=128, use_rotary_position_embeddings=False, rotary_base=1000000, rotary_percent=1.0, rotary_interleaved=False, rotary_seq_len_interpolation_factor=None, use_rope_scaling=False, rope_scaling_factor=8.0, add_position_embedding=False, mrope_section=None, make_vocab_size_divisible_by=128, normalization='RMSNorm', norm_epsilon=1e-05, apply_layernorm_1p=False, apply_residual_connection_post_layernorm=False, openai_gelu=False, squared_relu=False, swiglu=True, onnx_safe=None, bert_binary_head=True, untie_embeddings_and_output_weights=True, multi_latent_attention=False, mtp_num_layers=None, mtp_loss_scaling_factor=0.1, attention_d

In [3]:
print(type(args))

<class 'argparse.Namespace'>


In [3]:
import torch 
a=torch.load("/root/MG_test/mixtral/mixtral-mcore-TP1PP1EP2Layer1_2/iter_0000001/mp_rank_00_000/model_optim_rng.pt",weights_only=False)

In [ ]:
k=a["model"]
fc1= torch.cat([
                k["decoder.layers.0.mlp.experts.linear_fc1.weight0"],
                k["decoder.layers.0.mlp.experts.linear_fc1.weight0"]
            ], dim=0)
print(k["decoder.layers.0.mlp.experts.linear_fc1.weight0"].shape)
print(k["decoder.layers.0.mlp.experts.linear_fc2.weight0"].shape)


RuntimeError: Sizes of tensors must match except in dimension 0. Expected size 4096 but got size 14336 for tensor number 1 in the list.

In [19]:
from safetensors.torch import load_file
import torch

file_path1 = '/root/MG_test/checkpoints/mixtral/model-00001-of-00019.safetensors' # replace with your actual file path
file_path2 = '/root/MG_test/checkpoints/mixtral/model-00002-of-00019.safetensors' # replace with your actual file path
loaded = {}
loaded.update(load_file(file_path1))
loaded.update(load_file(file_path2))
loaded.keys()


dict_keys(['model.embed_tokens.weight', 'model.layers.0.block_sparse_moe.experts.0.w1.weight', 'model.layers.0.block_sparse_moe.experts.0.w2.weight', 'model.layers.0.block_sparse_moe.experts.0.w3.weight', 'model.layers.0.block_sparse_moe.experts.1.w1.weight', 'model.layers.0.block_sparse_moe.experts.1.w2.weight', 'model.layers.0.block_sparse_moe.experts.1.w3.weight', 'model.layers.0.block_sparse_moe.experts.2.w1.weight', 'model.layers.0.block_sparse_moe.experts.2.w2.weight', 'model.layers.0.block_sparse_moe.experts.2.w3.weight', 'model.layers.0.block_sparse_moe.experts.3.w1.weight', 'model.layers.0.block_sparse_moe.experts.3.w2.weight', 'model.layers.0.block_sparse_moe.experts.3.w3.weight', 'model.layers.0.block_sparse_moe.experts.4.w1.weight', 'model.layers.0.block_sparse_moe.experts.4.w2.weight', 'model.layers.0.block_sparse_moe.experts.4.w3.weight', 'model.layers.0.block_sparse_moe.experts.5.w1.weight', 'model.layers.0.block_sparse_moe.experts.5.w2.weight', 'model.layers.0.block_spa

In [20]:
import os
save_weights_dir="/root/MG_test/weights/"
for layer in range(2):
    for expert in range(8):
        w1_prefix = f'model.layers.{layer}.block_sparse_moe.experts.{expert}.w1.weight'
        w2_prefix = f'model.layers.{layer}.block_sparse_moe.experts.{expert}.w2.weight'
        w3_prefix = f'model.layers.{layer}.block_sparse_moe.experts.{expert}.w3.weight'
        target_prefix_fc1 = f"decoder.layers.{layer}.mlp.experts.linear_fc1.weight{expert}"
        target_prefix_fc2 = f"decoder.layers.{layer}.mlp.experts.linear_fc2.weight{expert}"
        target_prefix_fc1=save_weights_dir+target_prefix_fc1.replace(".","_")+".pt"
        target_prefix_fc2=save_weights_dir+target_prefix_fc2.replace(".","_")+".pt"
        fc1= torch.cat([
                loaded[w1_prefix],
                loaded[w3_prefix],
            ], dim=0)
        
        fc2= loaded[w2_prefix]
        
        torch.save(fc1,target_prefix_fc1)
        torch.save(fc2,target_prefix_fc2)
        

In [2]:
import os
import torch
save_weights_dir="/root/MG_test/weights/"
target_prefix_fc1 = f"decoder.layers.0.mlp.experts.linear_fc1.weight0"
path=target_prefix_fc1.replace(".","_")+".pt"
weight_fc1 = torch.load(path,weights_only=True)
weight_fc1

tensor([[-3.3569e-03,  1.0437e-02, -1.5747e-02,  ..., -1.6235e-02,
          5.2261e-04, -1.3062e-02],
        [-1.2360e-03,  2.0752e-03, -1.6968e-02,  ...,  1.7944e-02,
          1.0620e-02, -3.4943e-03],
        [-1.5869e-02,  1.9897e-02,  1.8845e-03,  ...,  1.8433e-02,
         -1.8921e-03, -5.2795e-03],
        ...,
        [-4.0894e-03,  1.5564e-02,  4.2152e-04,  ...,  5.8899e-03,
         -6.5994e-04,  7.8735e-03],
        [ 1.7334e-02,  7.5073e-03, -1.2146e-02,  ...,  1.6968e-02,
          4.5776e-03,  1.7456e-02],
        [ 2.1240e-02,  1.2756e-02,  1.0559e-02,  ...,  5.8289e-03,
          7.2937e-03,  6.6280e-05]], dtype=torch.bfloat16)

# Send request

In [1]:
import torch
import requests
tokens_per_expert = torch.tensor([32]*4, dtype=torch.int32).cpu().tolist()
dispatched_input = torch.randn(1, 32*4, 4096,
                                   dtype=torch.bfloat16).cpu().tolist()

url="http://localhost:5000/forward"

response = requests.post(
    url,
    json={
        'dispatched_input':dispatched_input,
        'tokens_per_expert':tokens_per_expert,
        'layer':'1'
        }  # 自动将字典转换为 JSON
)


print(response.json())


{'hidden_output': [[[-0.4375, 0.396484375, -0.048583984375, 0.1357421875, 0.91015625, 0.48046875, -0.138671875, -0.1513671875, 0.474609375, 0.60546875, -0.69140625, 0.265625, 0.1328125, -0.0732421875, -0.10107421875, -0.00543212890625, 0.1474609375, -0.67578125, 0.890625, 0.0279541015625, 0.037353515625, -0.625, -0.01171875, 0.5, -0.7890625, -0.361328125, 0.6875, 0.26171875, 0.33203125, -0.126953125, -0.30078125, -0.0299072265625, -0.2255859375, -0.051513671875, -0.470703125, 0.51171875, 0.734375, -0.015869140625, -0.248046875, 0.39453125, 0.53125, 0.54296875, -0.39453125, -0.93359375, 0.267578125, -0.640625, -0.09521484375, -0.255859375, -0.380859375, -0.05810546875, -0.017578125, 0.142578125, 0.453125, 3.90625, 0.11962890625, -0.54296875, 0.439453125, -0.333984375, -0.0203857421875, -0.1875, 0.392578125, 0.0245361328125, 0.33203125, 0.6640625, 0.32421875, 0.1591796875, 0.0908203125, 0.37109375, 0.224609375, -0.28125, -0.2578125, 0.75390625, 0.10302734375, -0.294921875, 0.80859375, 0.